# Homework 2

Least-squares, regularization, QR, and SVD

-   Name: Harry Potter
-   Student ID: 123456789

$$
\def\argmin{\operatorname*{argmin}}
\def\argmax{\operatorname*{argmax}}
\def\Ball{\mathbf{B}}
\def\bmat#1{\begin{bmatrix}#1\end{bmatrix}}
\def\Diag{\mathbf{Diag}}
\def\half{\tfrac12}
\def\int{\mathop{\rm int}}
\def\ip#1{\langle #1 \rangle}
\def\maxim{\mathop{\hbox{\rm maximize}}}
\def\maximize#1{\displaystyle\maxim_{#1}}
\def\minim{\mathop{\hbox{\rm minimize}}}
\def\minimize#1{\displaystyle\minim_{#1}}
\def\norm#1{\|#1\|}
\def\Null{{\mathbf{null}}}
\def\proj{\mathbf{proj}}
\def\R{\mathbb R}
\def\Re{\mathbb R}
\def\Rn{\R^n}
\def\rank{\mathbf{rank}}
\def\range{{\mathbf{range}}}
\def\sign{{\mathbf{sign}}}
\def\span{{\mathbf{span}}}
\def\st{\hbox{\rm subject to}}
\def\T{^\intercal}
\def\textt#1{\quad\text{#1}\quad}
\def\trace{\mathbf{trace}}
\def\xbar{\bar x}
$$

> **Homework submission instructions**
>
> -   See the [syllabus](../syllabus.qmd) for the due date
> -   Follow the [homework submission
>     instructions](submission-guide.qmd)

## P1. Quadratic fit to data

Consider the NO₂ [trendline
example](../notes/least-squares.qmd#sec-trendline) from the class notes.

-   Compute the coefficients $\alpha_1,\ldots\alpha_3$ that fit the
    quadratic model $$
    q(t) = \alpha_1 + \alpha_2 t + \alpha_3 t^2
    $$ to the detrended data (see the last plot of that example) in the
    least-squares sense.
-   Provide a plot of the detrended data and overlay the fitted function
    $q(t)$.

## P2. Iterative regularization

In [1]:
using LinearAlgebra, FFTW, Plots, Random

# Generate a signal using 4 random elements from the DCT basis.
function signal(n=200, k=4, ϵ=0.1)
    Random.seed!(19)
    x = zeros(n)
    p = randperm(n)[1:k]
    x[p] .= rand(k)
    noise = ϵ*randn(n)
    s = FFTW.dct(x) # true signal
    b = s + noise   # noisy signal
    return s, b
end

# Create an n-dimensional explicit Discrete Cosine Transform matrix.
function DCT(n::Integer)
    D = zeros(n, n)
    for i in 1:n
        e = zeros(n); e[i] = 1
        D[:,i] = FFTW.dct(e)
    end
    return D
end;

You observe the following noisy 1-D signal, which is stored in the
vector $b$. The true (and “unknown”) signal $s$ is displayed in blue.
(This is a contrived example — in practice, we would not know the true
signal.)

In [1]:
s, b = signal()
plot([s b], w = [2 1], label=["true signal `s`" "observed noisy signal `b`"])

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip450)" d="M254.873 1834 Q251.262 1834 249.433 1837.57 Q247.627 1841.11 247.627 1848.24 Q247.627 1855.34 249.433 1858.91 Q251.262 1862.45 254.873 1862.45 Q258.507 1862.45 260.313 1858.91 Q262.141 1855.34 262.141 1848.24 Q262.141 1841.11 260.313 1837.57 Q258.507 1834 254.873 1834 M254.873 1830.3 Q260.683 1830.3 263.739 1834.9 Q266.817 1839.49 266.817 1848.24 Q266.817 1856.96 263.739 1861.57 Q260.683 1866.15 254.873 1866.15 Q249.063 1866.15 245.984 1861.57 Q242.928 1856.96 242.928 1848.24 Q242.928 1839.49 245.984 1834.9 Q249.063 1830.3 254.873 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip450)" d="M808.754 1830.92 L827.111 1830.92 L827.111 1834.86 L813.037 1834.86 L813.037 1843.33 Q814.055 1842.98 815.074 1842.82 Q816.092 1842.64 817.111 1842.64 Q822.898 1842.64 826.277 1845.81 Q829.657 1848.98 829.657 1854.4 Q829.657 1859.97 826.185 1863.08 Q822.712 1866.15 816.393 1866.15 Q814.217 1866.15 811.949 1865.78 Q809.703 1865.41 807.296 1864.67 L807.296 1859.97 Q809.379 1861.11 811.601 1861.66 Q813.824 1862.22 816.3 1862.22 Q820.305 1862.22 822.643 1860.11 Q824.981 1858.01 824.981 1854.4 Q824.981 1850.78 822.643 1848.68 Q820.305 1846.57 816.3 1846.57 Q814.425 1846.57 812.55 1846.99 Q810.699 1847.4 808.754 1848.28 L808.754 1830.92 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip450)" d="M848.87 1834 Q845.259 1834 843.43 1837.57 Q841.624 1841.11 841.624 1848.24 Q841.624 1855.34 843.43 1858.91 Q845.259 1862.45 848.87 1862.45 Q852.504 1862.45 854.31 1858.91 Q856.138 1855.34 856.138 1848.24 Q856.138 1841.11 854.31 1837.57 Q852.504 1834 848.87 1834 M848.87 1830.3 Q854.68 1830.3 857.735 1834.9 Q860.814 1839.49 860.814 1848.24 Q860.814 1856.96 857.735 1861.57 Q854.68 1866.15 848.87 1866.15 Q843.06 1866.15 839.981 1861.57 Q836.925 1856.96 836.925 1848.24 Q836.925 1839.49 839.981 1834.9 Q843.06 1830.3 848.87 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip450)" d="M1412.2 1834 Q1408.58 1834 1406.76 1837.57 Q1404.95 1841.11 1404.95 1848.24 Q1404.95 1855.34 1406.76 1858.91 Q1408.58 1862.45 1412.2 1862.45 Q1415.83 1862.45 1417.64 1858.91 Q1419.46 1855.34 1419.46 1848.24 Q1419.46 1841.11 1417.64 1837.57 Q1415.83 1834 1412.2 1834 M1412.2 1830.3 Q1418.01 1830.3 1421.06 1834.9 Q1424.14 1839.49 1424.14 1848.24 Q1424.14 1856.96 1421.06 1861.57 Q1418.01 1866.15 1412.2 1866.15 Q1406.39 1866.15 1403.31 1861.57 Q1400.25 1856.96 1400.25 1848.24 Q1400.25 1839.49 1403.31 1834.9 Q1406.39 1830.3 1412.2 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip450)" d="M1442.36 1834 Q1438.75 1834 1436.92 1837.57 Q1435.11 1841.11 1435.11 1848.24 Q1435.11 1855.34 1436.92 1858.91 Q1438.75 1862.45 1442.36 1862.45 Q1445.99 1862.45 1447.8 1858.91 Q1449.63 1855.34 1449.63 1848.24 Q1449.63 1841.11 1447.8 1837.57 Q1445.99 1834 1442.36 1834 M1442.36 1830.3 Q1448.17 1830.3 1451.22 1834.9 Q1454.3 1839.49 1454.3 1848.24 Q1454.3 1856.96 1451.22 1861.57 Q1448.17 1866.15 1442.36 1866.15 Q1436.55 1866.15 1433.47 1861.57 Q1430.41 1856.96 1430.41 1848.24 Q1430.41 1839.49 1433.47 1834.9 Q1436.55 1830.3 1442.36 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip450)" d="M1981.42 1830.92 L1999.78 1830.92 L1999.78 1834.86 L1985.71 1834.86 L1985.71 1843.33 Q1986.72 1842.98 1987.74 1842.82 Q1988.76 1842.64 1989.78 1842.64 Q1995.57 1842.64 1998.95 1845.81 Q2002.33 1848.98 2002.33 1854.4 Q2002.33 1859.97 1998.85 1863.08 Q1995.38 1866.15 1989.06 1866.15 Q1986.89 1866.15 1984.62 1865.78 Q1982.37 1865.41 1979.97 1864.67 L1979.97 1859.97 Q1982.05 1861.11 1984.27 1861.66 Q1986.49 1862.22 1988.97 1862.22 Q1992.97 1862.22 1995.31 1860.11 Q1997.65 1858.01 1997.65 1854.4 Q1997.65 1850.78 1995.31 1848.68 Q1992.97 1846.57 1988.97 1846.57 Q1987.1 1846.57 1985.22 1846.99 Q1983.37 1847.

### P2(a) Least-squares solution

Obtain a guess of the underlying signal $s$ by solving a linear
least-squares problem with the DCT matrix $D$ as the basis. Plot the
recovered signal $\bar s$ on top of the true signal $s^\natural$. How
well does the least-squares solution recover the true signal?

### P2(b) Iterative regularization

Now suppose that we have knowledge that the signal $s^\natural$ (i.e.,
the signal without noise) is very uniform, and is in fact the
superposition of a few sinusoidal-like elements, such as are contained
in the columns of the [Discrete Cosine
Transform](https://en.wikipedia.org/wiki/Discrete_cosine_transform).
Here are the first five columns of the DCT matrix:

In [1]:
D = DCT(length(b))
plot(D[:, 1:5], xlims=(2, length(b)), leg=false)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip570)" d="M786.835 1830.92 L805.192 1830.92 L805.192 1834.86 L791.118 1834.86 L791.118 1843.33 Q792.136 1842.98 793.155 1842.82 Q794.173 1842.64 795.192 1842.64 Q800.979 1842.64 804.358 1845.81 Q807.738 1848.98 807.738 1854.4 Q807.738 1859.97 804.266 1863.08 Q800.794 1866.15 794.474 1866.15 Q792.298 1866.15 790.03 1865.78 Q787.784 1865.41 785.377 1864.67 L785.377 1859.97 Q787.46 1861.11 789.683 1861.66 Q791.905 1862.22 794.382 1862.22 Q798.386 1862.22 800.724 1860.11 Q803.062 1858.01 803.062 1854.4 Q803.062 1850.78 800.724 1848.68 Q798.386 1846.57 794.382 1846.57 Q792.507 1846.57 790.632 1846.99 Q788.78 1847.4 786.835 1848.28 L786.835 1830.92 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip570)" d="M826.951 1834 Q823.34 1834 821.511 1837.57 Q819.706 1841.11 819.706 1848.24 Q819.706 1855.34 821.511 1858.91 Q823.34 1862.45 826.951 1862.45 Q830.585 1862.45 832.391 1858.91 Q834.219 1855.34 834.219 1848.24 Q834.219 1841.11 832.391 1837.57 Q830.585 1834 826.951 1834 M826.951 1830.3 Q832.761 1830.3 835.817 1834.9 Q838.895 1839.49 838.895 1848.24 Q838.895 1856.96 835.817 1861.57 Q832.761 1866.15 826.951 1866.15 Q821.141 1866.15 818.062 1861.57 Q815.007 1856.96 815.007 1848.24 Q815.007 1839.49 818.062 1834.9 Q821.141 1830.3 826.951 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip570)" d="M1420.63 1834 Q1417.02 1834 1415.19 1837.57 Q1413.39 1841.11 1413.39 1848.24 Q1413.39 1855.34 1415.19 1858.91 Q1417.02 1862.45 1420.63 1862.45 Q1424.27 1862.45 1426.07 1858.91 Q1427.9 1855.34 1427.9 1848.24 Q1427.9 1841.11 1426.07 1837.57 Q1424.27 1834 1420.63 1834 M1420.63 1830.3 Q1426.44 1830.3 1429.5 1834.9 Q1432.58 1839.49 1432.58 1848.24 Q1432.58 1856.96 1429.5 1861.57 Q1426.44 1866.15 1420.63 1866.15 Q1414.82 1866.15 1411.75 1861.57 Q1408.69 1856.96 1408.69 1848.24 Q1408.69 1839.49 1411.75 1834.9 Q1414.82 1830.3 1420.63 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip570)" d="M1450.8 1834 Q1447.19 1834 1445.36 1837.57 Q1443.55 1841.11 1443.55 1848.24 Q1443.55 1855.34 1445.36 1858.91 Q1447.19 1862.45 1450.8 1862.45 Q1454.43 1862.45 1456.24 1858.91 Q1458.06 1855.34 1458.06 1848.24 Q1458.06 1841.11 1456.24 1837.57 Q1454.43 1834 1450.8 1834 M1450.8 1830.3 Q1456.61 1830.3 1459.66 1834.9 Q1462.74 1839.49 1462.74 1848.24 Q1462.74 1856.96 1459.66 1861.57 Q1456.61 1866.15 1450.8 1866.15 Q1444.99 1866.15 1441.91 1861.57 Q1438.85 1856.96 1438.85 1848.24 Q1438.85 1839.49 1441.91 1834.9 Q1444.99 1830.3 1450.8 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip570)" d="M2020.22 1830.92 L2038.58 1830.92 L2038.58 1834.86 L2024.5 1834.86 L2024.5 1843.33 Q2025.52 1842.98 2026.54 1842.82 Q2027.56 1842.64 2028.58 1842.64 Q2034.36 1842.64 2037.74 1845.81 Q2041.12 1848.98 2041.12 1854.4 Q2041.12 1859.97 2037.65 1863.08 Q2034.18 1866.15 2027.86 1866.15 Q2025.68 1866.15 2023.42 1865.78 Q2021.17 1865.41 2018.76 1864.67 L2018.76 1859.97 Q2020.85 1861.11 2023.07 1861.66 Q2025.29 1862.22 2027.77 1862.22 Q2031.77 1862.22 2034.11 1860.11 Q2036.45 1858.01 2036.45 1854.4 Q2036.45 1850.78 2034.11 1848.68 Q2031.77 1846.57 2027.77 1846.57 Q2025.89 1846.57 2024.02 1846.99 Q2022.17 1847.4 2020.22 1848.28 L2020.22 1830.92 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip570)" d="M2060.34 1834 Q2056.73 1834 2054.9 1837.57 Q2053.09 1841.11 2053.09 1848.24 Q2053.09 1855.34 2054.9 1858.91 Q2056.73 1862.45 2060.34 1862.45 Q2063.97 1862.45 2065.78 1858.91 Q2067.6 1855.34 2067.6 1848.24 Q2067.6 1841.11 2065.78 1837.57 Q2063.97 1834 2060.34 1834 M2060.34 1830.3 Q2066.15 1830.3 2069.2 1834.9 Q2072.28 1839.49 2072.28 1848.24 Q2072.28 1856.96 2069.2 1861.57 Q2066.15 1866.15 2060.34 1866.15 Q2054.53 1866.15 2051.45 1861.57 Q2048.39 1856.96 2048.39 1848.24 Q2048.39 1839.49 2051.45

The question, then, is how to choose the right columns of $D$ in order
to obtain a good guess of the underlying signal? In other words, is
there a sparse vector $x$ (i.e., one with just a few nonzeros) such that
$$
Dx \approx s?
$$ Equivalently, are there a few columns of $D$ whose span includes the
true signal $s$?

We’ll try to solve this problem by building up a solution $x$ element by
element. We do this by solving a sequence of least-squares problems of
increasing column dimension. The procedure begins with a trivial
solution $x_0 = 0$, associated residual $r_0 = b$, and an empty set of
columns $S_0 = [\ ]$. At each iteration $k>1$ of the procedure, we do
the following:

1.  Find the column of $D$ that is most correlated with the current
    residual $r_k$, i.e., find the index $j_0$ of the column
    $s_k := D[:, j_k]$ that maximizes $$
    \max_j\ |s_k^T r_k|.
    $$
2.  Stop if the correlation is small, i.e., if $|s_k^T r_k| < \tau$ for
    some threshold $\tau$.
3.  Append that column to the current set of columns to obtain
    $S_{k} = [\, \text{new col} \mid S_{k-1}\,]$.
4.  Obtain the next coefficient approximation $x_{k+1}$ and
    corresponding residual $r_{k+1}$ as the solution of the
    least-squares problem $$
    x_{k+1} := \arg\min_x\ \tfrac12\|S_k x - b\|^2.
    $$

Implement this procedure and plot the recovered signal $\hat s$
overlayed on the true signal $s^\natural$. How well does the iterative
regularization procedure recover the true signal? How many iterations
are required to obtain a good approximation?

## P3. Underdetermined systems

Show how to use the QR factorization to solve a full-rank
underdetermined system $Ax=b$ (i.e., $A$ is $m\times n$ with $m<n$ and
$\mathrm{rank}(A)=m$). Give an explicit procedure for solving this
system using the QR factors. Your procedure must only use matrix-vector
products and triangular solves. (Hint: consider using the thin QR
factorization of $A\T$.)

Demonstrate that your method works on a random $2\times 3$ system. These
functions may be useful:

``` julia
A = randn(m, n) # Gaussian random matrix
x = randn(n)    # and vector
```

## P4. (Beck 3.1) Tikhonov regularization

Fix the matrices $A\in\R^{m\times n}$ and $L\in\R^{n\times n}$. Consider
the regularized least-squares problem $$
\min_x\ \|Ax-b\|^2 + \|Lx\|^2.
$$ Show that this problem has a unique solution if and only if
$\Null(A)\cap\Null(L) = \{0\}$.

## P5. SVD and least-squares

The [Longley
dataset](https://www.itl.nist.gov/div898/strd/lls/data/Longley.shtml) is
a macroenomic dataset used extensively to evaluate the accuracy of
least-squares methods. It comprises 16 observations of 7 economic
variables recorded over the years 1947–1962.

In [1]:
using RDatasets, DataFrames
longley = dataset("datasets", "longley")
first(longley, 5)

Extract predictor variables and add an intercept column, and extract the
right-hand side:

In [1]:
A = hcat(ones(size(longley, 1)), longley[:, Not(:Employed, :Year_1)])|> Matrix
b = longley.Employed |> Vector

1.  Try to solve the least-squares problem using the QR decomposition.
    You’ll see that it will fail because the matrix $A$ is
    rank-deficient.
2.  Solve the least-squares problem using the SVD. You should remove any
    singular values that are below a certain threshold. A typical
    approach is to remove any singular value $$
    \sigma_i < \varepsilon \max_{ij}A_{ij},
    $$ where $\varepsilon$ is machine precision (e.g., `eps()` in
    Julia).
3.  In both parts (a) and (b), verify that the solution is indeed a
    least-squares solution by checking that the optimality condition
    $$\|A^T r\| < \varepsilon\|b\|
    $$ is satisfied, where $r = b - Ax$ is the residual. Good practice
    is to make consider a relative tolerance, say,

$$
\|A^T r\| < 10^{-8}\max(1,\|b\|).
$$

## P6. Singular values (Reichel)

Define the matrix $A$ with entries $$
a_{ij} = \sqrt{1-x_i^2 - y_j^2}, \quad x_i = y_i = -0.7+\Delta(i-1),\ \Delta=10^{-3}
$$ where $i,j=1,2,\ldots,1401$.

1.  Plot the matrix $A$ in 3D.
2.  Plot the first 50 singular values of $A$.
3.  Plot the error matrix $|A - A_k|$ (interpreted componentwise) where
    $A_k$ is the best rank-$k$ approximation to $A$. Choose $k$ to be
    the index of the largest singular value below $10^{-10}$. You may
    try a surface or contour plot.